# Game of Life - self-replicating systems with cellular automation
This is a zero player game created by John Horton Conway way back in 1970, where evolution is determined by some initial conditions after which you get to observe how the game evolves.
 
The game world is an infinite grid (in theory) of square 'cells' each of which could be in two possible states either alive or dead (or if you wish populated and unpopulated).

Every cell interacts with its eights neighbors (horizontally, vertically, and diagonally).

There are only 4 rules that govern this interaction and whether a cell emerges from the interaction alive or dead-

1. Any live cell with fewer than two live neighbors dies, as if by underpopulation.
2. Any live cell with two or three live neighbors lives on to the next generation.
3. Any live cell with more than three live neighbors dies, as if by overpopulation.
4. Any dead cell with exactly three live neighbors becomes a live cell, as if by reproduction.

All other cells (which ones do these pertain to by the way) keep their current life status unchanged.

The initial pattern (conditions) of the world grid constitutes the seed of the system, the first generation is created by applying the above rules simultaneously to every cell in this seed. Live, dead, births and deaths occur simultaneously - this happens during the discrete moement called a tick (you'll see what this means in the code and my way of handling it). Afterwhich, the rules continue to be applied repeatedly to create further generations.

Before looking at my implementation below, I encourage you to try to code this on your own from the rules only which is the route I went, throughout the process you'll learn so much and it really is alot of fun. Originally, amazingly, different tile patterns and how they evolve were discovered without computers by using blackboards and graph paper by hand.

It goes without saying that in my code the world is not infiinite - I've made it so my boundary cells (outside_boundary) can either be all dead or all alive (I defaulted to all alive but feel free to change it). 

When I first learned about this automation I was fasicnated and amazed at how such an interesting and dyamic system could be created from random intial conditions using four simple rules applied repeatedly. I love the simplicity and beauty of this automation, I hope you will too. Let's get to it-

## Modules and Defaults

In [1]:
#modules required
import numpy as np
import time
import scipy.signal as s #for our 2d convolution explained below

#for the visualization below here
import holoviews as hv
import panel as pn
pn.extension(design='material')# this enables panel using the material design/theme
from holoviews.streams import Pipe

#lookup for speed (alive_status,alive_neighbor_sum) : result
rules_look_up = {(1,0): 0, (1,1):0, (1,2):1, (1,3):1, (1,4):0, (1,5):0, (1,6):0, (1,7):0, (1,8):0, 
              (0,0): 0, (0,1):0, (0,2):0, (0,3):1, (0,4):0, (0,5):0, (0,6):0, (0,7):0, (0,8):0}


#we'll use this kernel to get our neighbor values 
kernel =[[1,1,1],
         [1,0,1],
         [1,1,1]]

#let's set up some defaults for our game, we'll be able to change most of these with panel widgets we'll see at the end
tick_delay = .15 # our tick delay in seconds
world_dim = 60 # our world is square world_dimxworld_dim
tick_life= 100 #how many steps (ticks) to run for
outside_boundary = 1 # cells outside boundary considered what, I kept it at 1 to allow the bounadires to be life giving :) 


## Making it fast!! What is a convolution anyways and how can that help us find the total number of 1's bordering a cell?
In this context, convolution involves taking a 3x3 kernel matrix and sliding it over our world matrix. We multiply each overlapping element and sum them up to obtain a result, which we store in the resulting matrix. If you pause to consider it, by multiplying first with the 3x3 kernel having a 0 in the middle we correctly mask out the middle and only look at neighbors and finally this summing process precisely helps us determine how many neighboring "1's" are alive, store this result in each cell and voila, you have neighbor-alive-count stored in every cell of our world.
A filter, or kernel, in a Convolutional Neural Network (CNN) is similarly small matrix of weights that slides over the input data, such as an image. It performs element-wise multiplication with the part of the input it is currently on and then sums up all the results into a single output pixel.
A couple of details to handle - what about the edges? If you simply align the kernel exactly with the input matrix, you might notice that you won't capture the edges. You wouldn't be able to slide the filter to all the cells, and your resulting output size would be smaller than your input. To address this issue and preserve the input size, we use the "same" mode with boundary (padding). By specifying mode='same' in our convolve2d function, we instruct it to add a boundary around the matrix. This allows us to slide our kernel to each cell while keeping the dimensions consistent with our input. The fill value lets us choose what to pad the matrix with; in our case, we can use either alive or dead cells (1 or 0) as the boundary.
Below is an example of how it works. Imagine sliding our 3x3 kernel over each position in the input, centering the 0 of the kernel over each cell. Since we have a boundary fill of 0, the overlapping parts that are outside of the boundaries will have 0's there, so we'll be fine. Check out the output of the cells below and verify that it does indeed get the number of alive neighbors. I'll cover the FTF and FFTF in a future blog post, but because the scipy function implements this, it makes calculating all these convolutions faster than manually running over a for loop to do it. Now we can have much bigger worlds without worrying about our frame rate plummeting. :)
Here's an example of this using the scipy.signal function convolve2d-



In [2]:
w = np.zeros((10,10), dtype=np.byte)

print(w)
conv_w = s.convolve2d(w, kernel,mode='same',boundary='fill',fillvalue = 1)
print('The number of alive (1) neighbors-\n',conv_w)


[[0 0 0 0 0 0 0 0 0 0]
 [0 0 0 0 0 0 0 0 0 0]
 [0 0 0 0 0 0 0 0 0 0]
 [0 0 0 0 0 0 0 0 0 0]
 [0 0 0 0 0 0 0 0 0 0]
 [0 0 0 0 0 0 0 0 0 0]
 [0 0 0 0 0 0 0 0 0 0]
 [0 0 0 0 0 0 0 0 0 0]
 [0 0 0 0 0 0 0 0 0 0]
 [0 0 0 0 0 0 0 0 0 0]]
The number of alive (1) neighbors-
 [[5 3 3 3 3 3 3 3 3 5]
 [3 0 0 0 0 0 0 0 0 3]
 [3 0 0 0 0 0 0 0 0 3]
 [3 0 0 0 0 0 0 0 0 3]
 [3 0 0 0 0 0 0 0 0 3]
 [3 0 0 0 0 0 0 0 0 3]
 [3 0 0 0 0 0 0 0 0 3]
 [3 0 0 0 0 0 0 0 0 3]
 [3 0 0 0 0 0 0 0 0 3]
 [5 3 3 3 3 3 3 3 3 5]]


## Rule Lookup -
I use a python dictionary (defined with the default parameters above) where each key represents the tuple 'alive_status, alive_neighbors'. By using data from both our current world matrix and the convolution matrix (precisely the matrices listed in the above output) we can quickly retrieve the evolved matrix with rules applied.

In [3]:
#lookup our rules with our dictionary by using our world matrix and the convoluted matrix to get the new alive status of each 
def lookup(world_status, alive_neighbors):
    global rules_look_up
    return rules_look_up[(world_status, alive_neighbors)]
vlookup = np.vectorize(lookup) # this is required so that it will run on all cells (basically act like a for loop) of what is passed in

## Main Game Tick -
This is the main part of the program that applies the rules and returns the evolved world along with some useful stats on the population and execution rate. To find the speed of game_tick you just compute 1 divided by how long it took to go through the function. This is a pretty small function considering everything that is going on.

In [30]:
def game_tick(world_view):
    time_tick = time.perf_counter() #perf_counter is more accurate than time.time()
    global outside_boundary #create our boundary border (PADDING if you will from CNN's)
    stable=True # keep track of if the population (# of 1's) changes or stays the same
    world_buffer = s.convolve2d(world_view, kernel,mode='same',boundary='fill',fillvalue = outside_boundary) #get the number of neighbors
    world_buffer = vlookup(world_view, world_buffer) # apply all the rules and store teh new state in teh world_buffer
    stable = (np.count_nonzero(world_view)==np.count_nonzero(world_buffer))#stable if the nonzero before and after ==  same population   
    time_tick = np.round(1 / (time.perf_counter()-time_tick)) # get the number this can be run per second
    return (world_buffer,f"** population {np.count_nonzero(world_view)} ** stable {stable} ** game_tick Speed {time_tick} calls per sec ") #return the modified world_buffer with stats
   

## Create our World -
Let's write a function to initialize our world so we can run this game over and over again.

In [31]:
#init the world with dimension dimxdim, random generated or not and eventually starting poitns
def init_world(dim, random=True,points=None):
    if random:
        create_world = np.random.randint(0,2,size=(dim,dim))
    else:
        create_world = np.zeros((dim,dim))
        if points is not None:
            for p in points: #if we pass intial points to try some inital conditions ourselves 
                if 0<=p[0]<create_world.shape[0] and 0<=p[1]<create_world.shape[1]:# make sure we're inside the world before we try to make alive  
                    create_world[p[0],p[1]]=1 
    return create_world #return our new world

## Our main game loop -
Now, let's integrate everything into a game loop, visualize it using the wonderful modules panel, and HoloViews. You'll be able to move and zoom around the world seamlessly.

In [62]:
# Create a Pipe stream to callback with the data to the holoview dynamic map Image, real time view
pipe = Pipe(np.zeros((700,700)))
#create a dynamic image representing our world you can experiment here with different color maps
image = hv.DynamicMap(hv.Image, streams=[pipe]).opts(
    width=600, height=600, xaxis=None, yaxis=None, toolbar=None,aspect='equal',cmap='viridis', border=0)

#now let's make our widgets so we can fiddle with defaults for our world
tick_delay_slider = pn.widgets.FloatSlider(name='tick_delay',start=.002, end=1,step=.002,value=tick_delay)
world_dim_slider = pn.widgets.IntSlider(name='world_size',start=10,end=1000,step=2,value=world_dim)
tick_life_slider = pn.widgets.IntSlider(name='world_life',start=20,end=10000,step=10,value=tick_life)
static_text = pn.widgets.StaticText(name='World Status', value='')
str_pane1 = pn.pane.Str('random world?')
random_switch = pn.widgets.Switch(name='Switch1', value=True)
str_pane2 = pn.pane.Str('boundaries alive?')
boundary_switch = pn.widgets.Switch(name='Switch2', value=True)
                        
#our main game loop where rules are applied and new world generations computed 
def game_loop(event):
    # make an intial world
    global outside_boundary
    outside_boundary=boundary_switch.value
    world = init_world(world_dim_slider.value,random=random_switch.value,points=None) 
    
    for i in range(tick_life_slider.value+1): #our main game loop       
        #data=np.random.randint(0,2,size=(world_dim_slider.value,world_dim_slider.value))
        (world,status) = game_tick(world) 
        #send another pipe stream to a text box or some other way just using panel?
        pipe.send(world)
        static_text.value=f"tick {i}/{tick_life_slider.value} {status} "
        time.sleep(tick_delay_slider.value)


button = pn.widgets.Button(name='Go')
button.on_click(game_loop) # link up our button to trigger the game_loop function we made

# put it all together to show to the world :) 
panel = pn.Column(pn.Row(world_dim_slider,tick_life_slider,tick_delay_slider),pn.Row(str_pane1,random_switch,str_pane2,boundary_switch),
                  pn.Row(button),pn.Row(static_text), image)
panel.servable() # (this creates a default layout as we) and shows everything ready to go!

Column(design=<class 'panel.theme.materi...)
    [0] Row(design=<class 'panel.theme.materi...)
        [0] IntSlider(design=<class 'panel.theme.materi..., end=1000, name='world_size', start=10, step=2, value=60)
        [1] IntSlider(design=<class 'panel.theme.materi..., end=10000, name='world_life', start=20, step=10, value=100)
        [2] FloatSlider(design=<class 'panel.theme.materi..., name='tick_delay', start=0.002, step=0.002, value=0.15)
    [1] Row(design=<class 'panel.theme.materi...)
        [0] Str(str, design=<class 'panel.theme.materi...)
        [1] Switch(design=<class 'panel.theme.materi..., value=True)
        [2] Str(str, design=<class 'panel.theme.materi...)
        [3] Switch(design=<class 'panel.theme.materi..., value=True)
    [2] Row(design=<class 'panel.theme.materi...)
        [0] Button(design=<class 'panel.theme.materi..., name='Go')
    [3] Row(design=<class 'panel.theme.materi...)
        [0] StaticText(design=<class 'panel.theme.materi..., name='World Status')
    [4] HoloViews(DynamicMap, design=<class 'panel.theme.materi..., height=600, sizing_mode='fixed', width=600)

# Final Thoughts -
I had such a great time creating this and spending far too long watching the 'spaceships' flying around :) .
The initial draft I wrote used a naive approach for finding neighbors (using for loops). As I considered ways to improve its efficiency, I realized it was simply summing up patches after applying a filter to exclude the middle. Convolution came to the rescue! By combining it with the fast SciPy version using FFT (Fast Fourier Transform), I was able to expand my world dimensions and achieve a rate of 7 with dimensions of 1000x1000. Not bad, considering that we apply the four rules to a million cells (1000x1000) each step - that's four million rule decisions for each game tick! 😊 Feel free to share any other algorithmic optimizations you might have in the comments below.
Perhaps you noticed in the code that I included a section in`init_world` for creating initial conditions points in a zero-filled world. Feel free to implement this if you'd like and let me know how it goes. You can find the latest version of this notebook on my GitHub- chrisblodgett/game_of_life (github.com) for those interested in downloading it.
I hope you enjoyed the experience, and maybe it even inspired you to create your own automations. Happy coding!